# Rasters 1: Intro to raster data

## Overview
1. Access real-time NWP data from Unidata's THREDDS server
2. Use Xarray's `plot.imshow` to display gridded data as an image
3. Use Xarray's `open_rasterio` method to open and view high-resolution elevation data
4. Close data objects when you are no longer using them.

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Xarray| Necessary | |

* **Time to learn**: 15 minutes
***

## Imports

In [ ]:
import xarray as xr
from datetime import datetime, timedelta

## Access real-time NWP data from Unidata's THREDDS server

Parse the current time and choose a recent hour when we might expect the model run to be complete. There is normally a ~90 minute lag, but we'll give it a bit more than that.

In [ ]:
now = datetime.now()
year = now.year
month = now.month
day = now.day
hour = now.hour
minute = now.minute
print (year, month, day, hour,minute)

In [ ]:
# The previous hour's data is typically available shortly after the half-hour, but give it a little extra time 
if (minute < 45): 
    hrDelta = 3
else:
    hrDelta = 2
runTime = now - timedelta(hours=hrDelta)
runTimeStr = runTime.strftime('%Y%m%d %H00 UTC')
modelDate = runTime.strftime('%Y%m%d')
modelHour = runTime.strftime('%H')
modelDay = runTime.strftime('%D')
print (modelDay)
print (modelHour)
print (runTimeStr)

Create an object pointing to the dataset.

In [ ]:
data_url = 'https://thredds.ucar.edu/thredds/dodsC/grib/NCEP/HRRR/CONUS_2p5km/HRRR_CONUS_2p5km_'+ modelDate + '_' + modelHour + '00.grib2'
data_url

In [ ]:
ds = xr.open_dataset(data_url)
xrdSize = ds.nbytes / 1e9
print ("Size of dataset = %.3f GB" % xrdSize)

In [ ]:
ds

<div class="alert alert-info">
    <b>Tip:</b> This Dataset, while stored in its native (GRIB2) format, presents itself to Xarray as NetCDF. The THREDDS server automatically translates GRIB to NetCDF. <br> Notice as well that its horizontal dimensions, <b>2145 x 1377</b>, differs from the HRRR datasets served via cloud providers such as AWS or Google Cloud <b>(1799 x 1099)</b>! The former is a bit higher in horizontal resolution (2.5 km vs 3 km).</div>

Note that the horizontal dimensions of this Dataset are not longitude/latitude. Instead, they represent distances in km from a central origin.

In [ ]:
ds.x

In [ ]:
ds.y

## Use Xarray's `plot.imshow` to display gridded data as an image

One of the output grids is surface pressure. We can visualize it as a proxy for surface elevation.

In [ ]:
ds.Pressure_surface

Use Xarray to generate an *image*, as opposed to a *filled contour* plot, for the first time in the `Dataset`.

In [ ]:
ds.Pressure_surface.isel(time1=0).plot.imshow(figsize=(15,10))

<div class="alert alert-danger">
    <b>WARNING:</b> A quirk in how a THREDDS data server interprets a GRIB dataset means that the coordinate variable names may change unpredictabily from run to run. In this case, the <i>time</i> dimension was named <code>time1</code>. When you run this notebook, the dimension name might also be <code>time1</code>, but it could be something else ... such as <code>time</code> or <code>time2</code> Modify the cell above if this occurs.</div>

<div class="alert alert-info">
    <b>Tip:</b> Rather than creating filled contours, we have used Xarray's Matplotlib interface to create an image map of surface pressure. Its resolution is the same as the dataset ... in this case, approximately 2.5 km. It fits the definition of what is called <i>raster</i> data.</div>

<div class="alert alert-warning">
    <b>Note:</b> But there exist other <i>rasterized</i> representations of elevation ... at even higher resolutions ... that are in a particular image format (<i>tiff</i>). Since we never expect these elevations to change (except on very long time scales), we can use these <i>static</i> datasets to complement our visualizations.</div>

## Use Xarray's `open_rasterio` method to open high-resolution elevation data</span> 

[Natural Earth](https://www.naturalearthdata.com/), the same source that Cartopy utilizes for many of the background features we have used, also provides raster datasets for download. The [medium](https://www.naturalearthdata.com/50m-manual-shaded-relief/manual-shaded-relief/) and [high](https://www.naturalearthdata.com/10m-manual-shaded-relief/manual-shaded-relief-of-contiguous-us/)-resolution manually-shaded relief files can be accessed from their location in the course data directory.

In [ ]:
ds50m = xr.open_rasterio('/spare11/atm533/data/raster/MSR_50M/MSR_50M.tif')
ds10m = xr.open_rasterio('/spare11/atm533/data/raster/US_MSR_10M/US_MSR.tif')

### Examine these Datasets

In [ ]:
ds50m

In [ ]:
ds10m

We now have two Xarray DataArray objects. They are three-dimensional (band, y, and x), with the new dimension called `band`. There is only one band in each of these data arrays, so we will just pass its one index (0) directly to `imshow`. Note the horizontal dimemsions ... in both cases, quite a bit higher than the already high-resolution HRRR grid we viewed above. What parts of the world do they represent?

In [ ]:
ds50m.sel(band=1).plot.imshow(figsize=(15,10))

In [ ]:
ds10m.sel(band=1).plot.imshow(figsize=(15,10))

<div class="alert alert-info">
    <b>Tip:</b> 
Notice the x- and y-axis labels. What do you think they represent? Look at the <i>attributes</i> for both of these data arrays for more info. Particularly notice the `crs` (Coordinate Reference System) attributes.
<br>We'll explore these <b>georeferenced TIFF (tagged image file format)</b> images in more detail in subsequent notebooks!</div>

In [ ]:
ds10m.crs

## Close the file handles so they don't stay resident in memory.

In [ ]:
ds.close()
ds10m.close()
ds50m.close()

---
## Summary
* We can access real-time NWP data via the [Unidata THREDDS server](https://thredds.ucar.edu)
* THREDDS automatically translates data in supported formats (such as GRIB) into NetCDF.
* Gridded data arrays are a type of **raster** data.
* Matplotlib's `imshow` method displays raster data as an image.
* A frequently-used image format is *tiff*.
* TIFFS can be geo-referenced, making them very useful in map-based visualizations.

### What's Next?
In the next notebook, we'll use our geo-referenced TIFF as a map layer and overlay NWP data on top of it.

## Resources and References
1. [Raster data (from Data Carpentry's Geospatial course)](https://datacarpentry.org/organization-geospatial/01-intro-raster-data)
1. [TIFF definition (Wikipedia)](https://en.wikipedia.org/wiki/TIFF)
1. [Python's Raster library (Rasterio)](https://rasterio.readthedocs.io)
